If you haven't heard about **mzQC** for your Quality Control operations, be assured, it is awesome. Not only does it provide you with a standardised way to store and exchange your QC data, but it is also super easy to get started with. Reading a mzQC file with the python library is super simple! I will demonstrate how simple in the next couple of minutes with a Jupyter python notebook. To start, just import our MZQCFILE module, open the file and read away...

In [1]:
from mzqc import MZQCFile as mzqc
with open('CPTAC_CompRef_00_iTRAQ_01_2Feb12_Cougar_11-10-09.mzQC', 'r') as mf:
    my_mzqc = mzqc.JsonSerialisable().FromJson(mf)

my_mzqc

If you are using this notebook in colab, you probably also need to install pymzqc to your runtime:

In [ ]:
%pip install pymzqc pandas plotly-express

:warning:  PRO-tip: try `my_mzqc.` and `tab` (for autocomplete) in a regular python REPL :warning:

It will list all available attributes and object members in an interactive fashion. And it will make exploration much much easier!

In [2]:
my_mzqc.description

'Clinical Proteomic Tumor Analysis Consortium Comparison and Reference (CompRef) Samples, initially characterized in the System Suitability Study, QC from the CPTAC Technology Assessment runs on Orbitrap instruments.'

In [3]:
my_mzqc.runQualities

In [4]:
my_run_qualities = my_mzqc.runQualities[0]

Why not some more exploration of the file tree? Also have a look at our [mzQC schema visualisation](https://raw.githubusercontent.com/HUPO-PSI/mzQC/main/schema/mzqc_schema.jpg), which explains the file structure in a more conservative fashion. After that, we should make sure that that's the mzQC for the run we wanted to make QC for.

In [5]:
my_run_qualities.metadata.inputFiles[0].name

'CPTAC_CompRef_00_iTRAQ_01_2Feb12_Cougar_11-10-09.trfr.t3.mzML'

Now, let's see what metrics we have in this file already.

In [6]:
for m in my_run_qualities.qualityMetrics:
    print(m.name)

DateTime of acquisition start
MS1 count
MS2 count
MZ aquisition range
RT aquisition range
MS1 Total ion current chromatogram
Chromatogram


Neat and concise for starters. And look, we have both the total ion chromatogram and the spectrophotometer chromatogram on record! Let's do something reaffirming to get going, by plotting the chromatograms. But first we quickly assign some more intelligible names for the objects we are going to access.

In [7]:
tic = my_run_qualities.qualityMetrics[5]
chrom = my_run_qualities.qualityMetrics[6]
rt_range = my_run_qualities.qualityMetrics[4]
ms2_number = my_run_qualities.qualityMetrics[2].value

In [8]:
import pandas as pd
tic_df = pd.DataFrame(tic.value) 
chrom_df = pd.DataFrame(chrom.value) 
tic_df['Chromatogram'] = "TIC"
chrom_df['Chromatogram'] = "Photometer"
df = tic_df.append(chrom_df)

import plotly.express as px
fig = px.line(df, y='int', x='RT', color='Chromatogram')
fig.show()

As expected, nothing out of the ordinary, awesome! Let's move on to something more challenging: add identifications. Imagine your analysis workflow produces a list of identifications in CSV format. No challenge for mzQC to integrate! We start by reading it into a DataFrame.

In [9]:
df = pd.read_csv("CPTAC_CompRef_00_iTRAQ_01_2Feb12_Cougar_11-10-09_ids.csv")
df

RT                                            peptide  target  \
0       69.8747   .(iTRAQ4plex)M(Oxidation)C(Carbamidomethyl)HNVNR    True   
1       80.2456  .(iTRAQ4plex)THHHLC(Carbamidomethyl)C(Carbamid...    True   
2       85.0696  .(iTRAQ4plex)THHHLC(Carbamidomethyl)C(Carbamid...    True   
3      115.3237  .(iTRAQ4plex)THHHLC(Carbamidomethyl)C(Carbamid...    True   
4      150.5772  .(iTRAQ4plex)K(iTRAQ4plex)SC(Carbamidomethyl)H...    True   
...         ...                                                ...     ...   
6861  5957.8817  .(iTRAQ4plex)VIHDNFGIVEGLMTTVHAITATQK(iTRAQ4plex)    True   
6862  5958.8237  .(iTRAQ4plex)SGTIFDNFLITNDEAYAEEFGNETWGVTK(iTR...    True   
6863  5960.2000                               .(iTRAQ4plex)LTGMAFR    True   
6864  5962.2214                         .(iTRAQ4plex)VNADEVGGEALGR    True   
6865  5966.2135           .(iTRAQ4plex)DLVVLLFETALLSSGFSLEDPQTHSNR    True   

              MZ  deltaPPM  
0     364.171234 -1.005341  
1     422.200562 -2.891580  
2     316.902832 -1.021924  
3     316.903137 -0.058930  
4     435.242188 -1.757828  
...          ...       ...  
6861  577.518921  0.493518  
6862  889.930725  0.345657  
6863  470.264862  2.350391  
6864  715.869568 -2.605892  
6865  783.912598 -1.534270  

[6866 rows x 5 columns]

FDR filtered already, iTRAQ label detected, looks good. A little more affirmatory visualisation, please. Plot the error distribution.

In [10]:
import plotly.figure_factory as ff
fig = ff.create_distplot([df.deltaPPM], ['deltaPPM'])
fig.show()

So far looks good, maybe some time later revisit those few outliers (homework). For now, let's see what else we can calculate from the data we've got.
```
[Term]
id: QC:4000189
name: ID ratio
def: "The ratio of identified and recorded MS2 spectra after FDR filtering." [PSI:QC]
is_a: QC:4000003 ! single value
is_a: QC:4000009 ! ID based
is_a: QC:4000001 ! QC metric
relationship: has_units STATO:0000300 ! dimensionless ratio
```
This sounds like a good start! Let's create our first QualityMetric object. We can use the length of any column in the DataFrame as the numerator, the number of MS2 spectra for the denominator we've already asigned a handy name earlier on.

In [11]:
new_metric = mzqc.QualityMetric(accession="QC:4000189",
                        name="ID ratio",
                        value=df.RT.size / ms2_number)
new_metric.value

0.4635430731839049

Now we add the object to our mzQC file. 

In [12]:
my_run_qualities.qualityMetrics.append(new_metric)

That's it, just as easy as this. Let's calculate a slightly more elaborate metric. 
```
[Term]
id: QC:4000072
name: Interquartile RT period for peptide identifications
def: "The interquartile retention time period, in seconds, for all peptide identifications over the complete run." [PSI:QC]
comment: Longer times indicate better chromatographic separation.
is_a: QC:4000003 ! single value
is_a: QC:4000009 ! ID based
is_a: QC:4000022 ! chromatogram metric
relationship: has_relation QC:4000013 ! QC metric relation: single run
```
This looks like a good candidate to continue. For that, we'll need the list of retention times of identifications (already in chronological order) and determine the quartiles, that is at which _RT_ a quarter (Q1) and 3/4 (Q3) of all identifications have happened. There is a handy DataFrame built-in method to do this very thing. *phew!*

In [13]:
ids_q1, ids_q3 = df.RT.quantile([0.25,0.75])
next_metric = mzqc.QualityMetric(accession="QC:4000072",
                        name="Interquartile RT period for peptide identifications",
                        value=ids_q3 - ids_q1)
my_run_qualities.qualityMetrics.append(next_metric)
next_metric.value

2395.09015

Just to put this into perspective, let's see what half of the overall RT period is.

In [14]:
import numpy as np
duration_rt = np.diff(rt_range.value)[0]
duration_rt/2

2984.76065

That means, the _middle_ half of the identifications was created in less than half the overall retention time period. Chromatographic separation could be interpreted as narrow, but this will also depend on the other runs in that batch. For now we'll leave that be. 
But at last, lets save our progress to file and have a look. Just as loading, writing is just as easy after you've added the new metrics (we did that earlier). 

In [15]:
with open('CPTAC_CompRef_00_iTRAQ_01_2Feb12_Cougar_11-10-09.updated.mzQC', 'w') as mf:
    mf.write(mzqc.JsonSerialisable().ToJson(my_mzqc, 2))
